# Université Paris-Saclay, Master 1 Mécanique des Fluides, Année 2023-2024

# _Méthodes Numériques pour la Mécanique des Fluides_

# Examen - 29 mars 2024 

Durée de l'épreuve : 3 heures

Documents de cours et de TP non autorisés

Les réponses seront données sur la **copie d'examen**, sauf pour les questions nécessitant de la programmation.


# III. Méthode spectrale Fourier

## III.1 Compréhension du code
Ci-dessous, le code qui donne la solution du TP2. 

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

def om_init(X,Y):
    
    #fonction qui calcule la vorticité initiale     
    epsilon=1
    sigma=0.1
    A1=10.
    A2=A1
    om=A1*np.exp(-((X-np.pi-epsilon)**2+(Y-np.pi)**2)/(2*sigma))+A2*np.exp(-((X-np.pi+epsilon)**2+(Y-np.pi)**2)/(2*sigma))
    return om

def NS2Dspec(Re,M,T,dt,nsave):

    #fonction locale pour calculer terme NL
    def NLcalcul(f_psi,f_om):

        #evaluer les derivees dans l'espace spectrale 
        #revenir dans l'espace physique
        dpsidx=np.fft.ifft2(1j*KX*f_psi)
        dpsidy=np.fft.ifft2(1j*KY*f_psi)
        domdx=np.fft.ifft2(1j*KX*f_om)
        domdy=np.fft.ifftn(1j*KY*f_om)
       
        #transformer dans l'espace de fourier et enlever erreur de aliasing
        f_NL=np.fft.fft2(-dpsidy*domdx+dpsidx*domdy)*FILT
    
        return f_NL
    
    ## nombre de pas de temps et temps discrets
    N=round(T/dt)
    
    ## maillage spatial et spectral
    xlist=np.arange(0,M)*2*np.pi/M
    ylist=np.arange(0,M)*2*np.pi/M
    X,Y=np.meshgrid(xlist,ylist)
    
    kxlist=np.concatenate([np.arange(0,M/2),np.arange(-M/2,0)])
    kylist=np.concatenate([np.arange(0,M/2),np.arange(-M/2,0)])   
    KX,KY=np.meshgrid(kxlist,kylist)

    ## matrices 
    K2=KX**2+KY**2

    O1=(1-dt/(2*Re)*K2)/(1+dt/(2*Re)*K2) 
    O2=dt/(1+dt/(2*Re)*K2) 
  
    K2inv=1./K2
    K2inv[0,0]=0  #attention pour le mode kx=ky=0, qui n'existe pas, sinon on aura oo

    FILT=np.sqrt(K2)<(M/3)
    
    ##Initialisation
    omn=om_init(X,Y) #appel à la fonction d'initialisation

    f_omn=np.fft.fft2(omn)*FILT
    f_psin=K2inv*f_omn

    #terme non-lineare pas a temps 0 et -1
    f_NLn=NLcalcul(f_psin,f_omn);

    #Adam Bshfort demande un terme NL au temps -1 qu'on ne connait pas
    #on fait donc un premier pas de Euler explicite pour le
    # terme non-lineaire
    f_NLnm1=np.copy(f_NLn) 

    # Tableaux contenant le champ de vorticite
    N_tout=N//nsave+1
    OMmat=np.zeros([M,M,N_tout])  #matrice 3D, avec zeros, dimension M x M x nombre de pas de temps sauvegardés  
    OMmat[:,:,0]=omn
    compte=1        # Compteur


    # Tableaux pour temps
    t_save=np.zeros(N_tout)#vecteur avec zeros, dimension nombre de pas de temps sauvegardés   
    t_save[0]=0

    #boucle principale
    for np1 in range(1,N+1): #pour n allant de 1 a N
                      
        # schema numerique
        f_omnp1=O1*f_omn+O2*(3/2*f_NLn-1/2*f_NLnm1)
        f_psinp1=K2inv*f_omnp1
    
        E=1/M**2*np.sum(np.abs(f_omnp1)**2)   
        if E>1e+10:
            break        
  
        # enregistrer champ si necessaire
        if np1%nsave==0:
        
            OMmat[:,:,compte]=np.real(np.fft.ifft2(f_omnp1)) #on veut le champ dans l'espace physique
            t_save[compte]=np1*dt
        
            #imprimer un message a l'ecran pour suivre la progression du calcul
            print('---------------------------------------')
            print(np1,' pas sur ',N)
       
            #incrementer le compteur 
            compte=compte+1
    
        #glissement des variables, pour preparer pas suivant
        f_omn=np.copy(f_omnp1)
        f_psin=np.copy(f_psinp1)
             
        #termes NL, pour preparer pas suivant
        f_NLnm1=np.copy(f_NLn)
        f_NLn=NLcalcul(f_psin,f_omn)

        
    return X,Y,OMmat,t_save

Quelques instructions pour lancer le calcul

In [ ]:
Re,M,T,dt,nsave=500,200,10,0.005,50
X,Y,OMmat,t_save=NS2Dspec(Re,M,T,dt,nsave)

et pour le visualiser

In [ ]:
import matplotlib.pyplot as plt
import matplotlib.animation
from mpl_toolkits.axes_grid1 import make_axes_locatable
plt.rcParams["animation.html"] = "jshtml"
plt.ioff()

fig = plt.figure(figsize=(8,8))
ax = fig.add_subplot(1, 1, 1)
time_template = 't = %.2fs'
time_text = ax.text(2,1.1,'') 
plt.set_cmap('jet')
cont = ax.contourf(X,Y,OMmat[:,:,0],20)
ax.set_xlabel('x')
ax.set_ylabel('y')
ax.axis('equal')
# I like to position my colorbars this way, but you don't have to
div = make_axes_locatable(ax)
cax = div.append_axes('right', '5%', '5%')

#sortie graphique
def update(n):
    global cont
    for c in cont.collections:
        c.remove()  # removes only the contours, leaves the rest intact
    cont = ax.contourf(X,Y,OMmat[:,:,n],20)
    cax.cla() # clear current axes (colormap)
    fig.colorbar(cont, cax=cax,label='Omega') # set new colormap with new values
    time_text.set_text(time_template%t_save[n])
    return cont, time_text

step=10
matplotlib.animation.FuncAnimation(fig, update, frames=range(0,round(round(T/dt)/nsave),step), repeat=False)    


## Questions partie III.1 :  se reporter au sujet d'examen


## III.2 Programmation: méthode de projection de Chorin


Se reporter au sujet d'examen.


## Programmation 

Compléter les quelques lignes laissés vide dans le programme ci-dessous afin d'implémenter cette méthode de projection. 

In [ ]:
import numpy as np
def om_init(X,Y):
    
    #fonction qui calcule la vorticité initiale     
    epsilon=1
    sigma=0.1
    A1=10.
    A2=A1
    om=A1*np.exp(-((X-np.pi-epsilon)**2+(Y-np.pi)**2)/(2*sigma))+A2*np.exp(-((X-np.pi+epsilon)**2+(Y-np.pi)**2)/(2*sigma))
    return om

def NS2Dspec_chorin(Re,M,T,dt,nsave):

    #fonction locale pour calculer terme NL
    def NLcalcul(f_u,f_v):

        ...
        
        return f_NLx, f_NLy
    
    ## nombre de pas de temps et temps discrets
    N=round(T/dt)
    
    ## maillage spatial et spectral
    xlist=np.arange(0,M)*2*np.pi/M
    ylist=np.arange(0,M)*2*np.pi/M
    X,Y=np.meshgrid(xlist,ylist)
    
    kxlist=np.concatenate([np.arange(0,M/2),np.arange(-M/2,0)])
    kylist=np.concatenate([np.arange(0,M/2),np.arange(-M/2,0)])   
    KX,KY=np.meshgrid(kxlist,kylist)

    ## matrices 
    K2=KX**2+KY**2  
    K2inv=1./K2
    K2inv[0,0]=0  
    FILT=np.sqrt(K2)<(M/3)
    

    ##Initialisation
    omn=om_init(X,Y) #appel à la fonction d'initialisation
    f_omn=np.fft.fft2(omn)*FILT
    
    #initialiser f_un et f_vn à l'aide de f_omn et les matrices
    f_un=...
    f_vn=...
    
    f_NLx,f_NLy=NLcalcul(f_un,f_vn)

    # Tableaux 
    N_tout=N//nsave+1
    OMmat=np.zeros([M,M,N_tout])   # on exporte la vorticité pour comparer plus facilement au code précédent
    OMmat[:,:,0]=np.real(np.fft.ifft2(1j*KX*f_vn-1j*KY*f_un))
    compte=1        

    t_save=np.zeros(N_tout)  
    t_save[0]=0

    #O1 : vous avez besoin d'une matrice pour calculer la vitesse auxiliaire
    O1=...
    
    #boucle principale
    for np1 in range(1,N+1): #pour n allant de 1 a N
                      
        # schema numerique de Chorin (les trois étapes)
        f_ustar=...
        f_vstar=...
        
        f_phi=...
        
        f_unp1=...
        f_vnp1=...
        
        E=1/M**2*np.sum(np.abs(f_unp1)**2+np.abs(f_vnp1)**2)         
        if E>1e+10:
            break        
  
        # enregistrer champ si necessaire
        if np1%nsave==0:
        
            OMmat[:,:,compte]=np.real(np.fft.ifft2(1j*KX*f_vn-1j*KY*f_un))
            t_save[compte]=np1*dt
        
            #imprimer un message a l'ecran pour suivre la progression du calcul
            print('---------------------------------------')
            print(np1,' pas sur ',N)
       
            #incrementer le compteur 
            compte=compte+1
    
        f_un=...
        f_vn=...
             
        f_NLx,f_NLy=NLcalcul(f_un,f_vn)

        
    return X,Y,OMmat,t_save

Pour lancer le calcul

In [ ]:
Re,M,T,dt,nsave=500,200,2,0.001,50
X,Y,OMmat,t_save=NS2Dspec_chorin(Re,M,T,dt,nsave)

Pour afficher la vorticité on utilise la fonction précédente du TP2

In [ ]:
step=5
matplotlib.animation.FuncAnimation(fig, update, frames=range(0,round(round(T/dt)/nsave),step), repeat=False)    

Si tout est correct, vous devez voir à peu près la même chose qu'avec la méthode utilisée en TP2. 